In [27]:
# using DifferentialEquations
# 

using Plots
# using PyCall

plotlyjs()

# http://spencerlyon.com/PlotlyJS.jl/examples/line_scatter/

Plots.PlotlyJSBackend()

## 9.1 MM, GG and RinzelHH 
Based on equation 9.3

In [2]:
function MM(V)
    # Na action variable
    U = -V - 70
    Alpha = 0.1*(U + 25)./(exp((U+25)/10) - 1)
    Beta = 4*exp(U/18)
    return Alpha./(Alpha + Beta)
end

function GG(V)
    # Equilibrium value of recovery variable W for Hodgkin-Huxley Equations
    S = 1.2714
    U = -V - 70 # for new Rinzel system
    AH = 0.07*exp(U/20)
    BH = (1 + exp((U+30)/10)).^(-1)
    Hh = AH./(AH + BH);  # Na+ inactivation variable
    AN = 0.01*(U+10)./(exp((U+10)/10) - 1)
    BN = 0.125*exp(U/80)
    Nn = AN./(AN + BN)
    return S*(Nn + S*(1 - Hh))./(1 + S^2)
end

function Vnull(W, VX, IE)
    # dV/dt = 0 isocline for Rinzel
    S = 1.2714
    U = -VX - 70  # For new Rinzel formulation
    Alpha = 0.1*(U + 25)./(exp((U+25)/10) - 1)
    Beta = 4*exp(U/18)
    M = Alpha./(Alpha + Beta + 0.000001)
    Result =(IE - 120*M^3*(1-W)*(VX-55) - 36*(W/S)^4*(VX+92) - 0.3*(VX+50.528))^2
end

Vnull (generic function with 1 method)

# RinzelHH.m

In [3]:
#This particular variation has VNa = +55; VK = -92, and VL = -50.52
#Solution of Rinzel-Hodgkin-Huxley Equations
#Tempreature of 16.3 deg C
#The resting potential is -70 mV
DT = 0.02;  #Time increment in msec.
Last = 1000;  #Last time step
Time = DT*[1:Last];  #Time vector
V = zeros(1, Last);  #Vectors to store results
W = zeros(1, Last)
IE = 5# input("Stimulating current (range 0-200): ");  #External Current
S = 1.2714
V[1] = -70;  #Put initial conditions here
W[1] = 0.40388;  #This is the resting value

for T = 2:Last
    VV = V[T-1]
    WW = W[T-1]
    IEE = IE
    for RK = 1:2  #Second Order Runge-Kutta
        M = MM(VV)  #This and following lines calculate V dependent terms
        Geq = GG(VV)  #Winfinity or equilibrium value
        Tau = 5*exp.(-(VV+60)^2/55^2) + 1
        V[T] = V[T-1] + (RK/2)*DT*(IEE - 120*M^3*(1-WW)*(VV-55) - 36*(WW/S)^4*(VV+92) - 0.3*(VV+50.528))
        W[T] = W[T-1] + (RK/2)*DT*(3*(Geq - WW)/Tau)
        VV = V[T]
        WW = W[T]
    end
end

WS = (W - 0.40388)*100 - 70;  #Scaled to approximate units


# Wnull = -99:4:61

# S = 1.2714
# U = -Wnull - 70;  #for new Rinzel system()
# AH = 0.07*exp.(U/20)
# BH = (1 + exp.((U+30)/10)).^(-1)
# Hh = AH./(AH + BH);  #Na+ inactiWnullation Wnullariable
# AN = 0.01*(U+10)./(exp.((U+10)/10) - 1)
# BN = 0.125*exp.(U/80)
# Nn = AN./(AN + BN)
# DW = S*(Nn + S*(1 - Hh))./(1 + S^2)


# # WW = zeros(23)
# # Vplot = linspace(90, 54, length(WW))
# # x = linspace(0, .95, 100)
# # for j = 1:3#23
# #     VX = Vplot[j]
# #     WW[j] = fminbnd(Vnull, .1, .95) # THIS FUNCTION DOES NOT EXIST IN JULIA
# #     @show WW[j]
# # end

# # Only plot Wnull vs DW and V vs W
# # PF = plot(Wnull, DW, "-b", Vplot, WW, "-k", V, W, "-r")
# plot(Wnull, DW, "-b")
# scatter(V, W )
# axis([-100, 60, 0, 1])
# xlabel("V") 
# ylabel("R")
# title("Phase Plane, dV/dt = 0 (black), dR/dt = 0 (blue) & limit cycle (red)")



In [4]:

trace1 = PlotlyJS.scatter(;x=Array{Float64}(Time[1])[:], y=V[:], mode="lines")
layout = PlotlyJS.Layout(title="RinzelHH")
p = PlotlyJS.plot([trace1], layout);

p

# linescatter1(Array{Float64}(Time[1][:]), V[:])

# HHWeq.m

In [5]:

#Fourth Order Runge-Kutta for N-Dimensional Systems

Total_Neurons = 2  #Solve for this number of interacting Neurons
DT = 0.02  #Time increment as fraction of time constant
Final_Time = 20   #Final time value for calculation
Last = Int64(Final_Time./DT + 1)  #Last time step
Time = DT*(0:Last-1)  #Time vector
Tau = 0.8  #Neural time constants in msec
TauR = 1.9
WTS = [1 2 2 1]  #Runge-Kutta Coefficient weights


X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)



for NU = 1:Total_Neurons  #Initialize
    X[NU, :] = zeros(1, Last)  #Vector to store response of Neuron #1
    K[NU, :] = zeros(1, 4)  #Runge-Kutta terms	
    Weights[NU, :] = WTS #Make into matrix for efficiency in main loop
end

X[1, 1] = -0.70  #Initial conditions here if different from zero
X[2, 1] = 0.088  #Initial conditions here if different from zero
Wt2 = [0 .5 .5 1] #Second set of RK weights
rkIndex = [1 1 2 3]
Stim = 1#input("Stimulating current strength (0-2): ")

for T = 2:Last
    for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]

        K[1, rk] = DT/Tau*(-(17.81 + 47.71*XH[1] + 32.63*XH[1]^2)*(XH[1] - 0.55) - 26*XH[2]*(XH[1] + 0.92) + Stim);  
        K[2, rk] = DT/TauR*(-XH[2] + 1.35*XH[1] + 1.03)
 end
    X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
end


#plot(Time, 100*X[1,:])
xlabel!("Time (ms)")


VV = -0.9:0.01:1.5
DVdt = -0.5*((1.37 + 3.67.*VV + 2.51.*VV.^2).*(VV - 0.55) - Stim/13)./(VV + 0.92)
DRdt = 1.35*VV + 1.03
# figure(2)
#ZB = plot(VV, DVdt, "k-", VV, DRdt, "b-", X[1, :], X[2, :], "r-")


-0.18500000000000005:0.013500000000000002:3.055

In [6]:

trace1 = PlotlyJS.scatter(;x=Time, y=100.*X[1,:], mode="lines")
layout = PlotlyJS.Layout(;title="Spike rate over time")
p1 = PlotlyJS.plot([trace1], layout)

trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="blue", name="VV vs DVdt")
trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="black", name="VV vs DRdt")
trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red", name="X[1, :] vs X[2, :]")
layout = PlotlyJS.Layout(;title="HHWEqu", xaxis_range=[-1, .6], yaxis_range=[0, 1])
p2 = PlotlyJS.plot([trace1, trace2, trace3], layout)



# HHWhysteresis.m

In [7]:

Total_Neurons = 2  #Solve for this number of interacting Neurons
DT = 0.02  #Time increment as fraction of time constant
FS = 2#input("Type 1 for fast ramp or 3 for slow ramp: ")
Final_Time = FS*100  #Final time value for calculation
Last = Int64(Final_Time./DT + 1) #Last time step
Time = DT*(0:Last-1)  #Time vector
Tau = 0.8  #Neural time constants in msec
TauR = 1.9
WTS = [1 2 2 1] #Runge-Kutta Coefficient weights

X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)

for NU = 1:Total_Neurons  #Initialize
    X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
    K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
    Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
end

Stimulus = zeros(Last)

X[1, 1] = -0.70  #Initial conditions here if different from zero
X[2, 1] = 0.09  #Initial conditions here if different from zero
Wt2 = [0 .5 .5 1]  #Second set of RK weights
rkIndex = [1 1 2 3]
Stim = 1#input("Stimulating current strength (0-2): ")

RL = FS*50;  #Ramp Length : Duration of half of triangular stimulation

ST = 10.6
for T = 2:Last
    for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
        Tme = Time[T-1] + Wt2[rk]*DT;  #Time upgrade
        global Tme
        K[1, rk] = DT/Tau*(-13*(1.37 + 3.67*XH[1] + 2.51*XH[1]^2)*(XH[1] - 0.55) - 26*XH[2]*(XH[1] + 0.92) + Stim*Tme/RL*(Tme <= RL) + Stim/RL*(2*RL - Tme)*(Tme > RL));  
        K[2, rk] = DT/TauR*(-XH[2] + 1.35*XH[1] + 1.03)

    end
    X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
    Stimulus[T] = Stim*Tme/RL*(Tme <= RL) + Stim/RL*(2*RL - Tme)*(Tme > RL)
end

# figure(1)
# ZA = plot(Time, 100*X[1, :], "r-", Time, Stimulus*200 - 100, "b-")
# print("DEBUG\n")
# xlabel("Time (ms)")
# ylabel("V(t) (red) & Current Ramp (blue")
VV = -0.9:0.01:1.5
DVdt = -0.5*((1.37 + 3.67*VV + 2.51*VV.^2).*(VV - 0.55) - Stim/13)./(VV + 0.92)
DRdt = 1.35*VV + 1.03
# figure(2) 
# ZB = plot(VV, DVdt, "k-", VV, DRdt, "b-", X[1, :], X[2, :], "r-")


-0.18500000000000005:0.013500000000000002:3.055

In [8]:
# ZA = plot(Time, 100*X[1, :], "r-", Time, Stimulus*200 - 100, "b-")
# ZB = plot(VV, DVdt, "k-", VV, DRdt, "b-", X[1, :], X[2, :], "r-")

trace1 = PlotlyJS.scatter(;x=Time, y=100(X[1, :]), mode="lines", line_color="red")
trace2 = PlotlyJS.scatter(;x=Time, y=Stimulus*200-100, mode="lines", line_color="blue")
layout = PlotlyJS.Layout(;title="Voltage (red) and Current Ramp (blue) vs Time (ms)", xaxis_range=[minimum(Time), maximum(Time)],
                     yaxis_range=[-100, 100])
PlotlyJS.plot([trace1, trace2], layout)


In [9]:

trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="black")
trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="blue")
trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red")
layout = PlotlyJS.Layout(;title="Phase Space", xaxis_range=[-1, .5], yaxis_range=[-1, 1])
PlotlyJS.plot([trace1, trace2, trace3], layout)

# HHnoise.m (still need to finish Histogram)

In [10]:


Total_Neurons = 2;  #Solve for this number of interacting Neurons
DT = 0.02;  #Time increment as fraction of time constant
Final_Time = 500;   #Final time value for calculation
Last = Int64(Final_Time/DT + 1);  #Last time step
Time = DT*[0:Last-1];  #Time vector
Tau = 0.8;  #Neural time constants in msec
TauR = 1.9;
WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)

for NU = 1:Total_Neurons;  #Initialize
    X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
    K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
    Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
end
X[1, 1] = -0.70;  #Initial conditions here if different from zero
X[2, 1] = 0.088;  #Initial conditions here if different from zero
Wt2 = [0 .5 .5 1];  #Second set of RK weights
rkIndex = [1 1 2 3]
Stim = 1#input("Stimulating current amplitude (0-2): ")
SDnoise = 1#input("Standard Deviation of noise = ")
Freq = 80#input("Stimulus frequency in Hz (> 50) = ")

for T = 2:Last
    for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
        Tme =Time[1][T-1] + Wt2[rk]*DT;  #Time upgrade
        
        global Stim, freq, Tme, SDnoise, DT, Tau, XH, rk
        K[1, rk] = DT/Tau.*(-(17.81 + 47.71.*XH[1] + 32.63.*XH[1]^2)*(XH[1] - 0.55) - 26.*XH[2].*(XH[1] + 0.92) + Stim.*sin(2.*pi.*Freq.*Tme./1000) + rand().*SDnoise);  
        K[2, rk] = DT/TauR*(-XH[2] + 1.35*XH[1] + 1.03)

    end
    X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
end




In [11]:

Ptime = 0:0.1:200
SineWave = 10*sin(2*pi*Ptime*Freq/1000)-100
# figure(1), ZA = plot(Time, 100*X[1, :], "r-', Ptime, SineWave, 'b-")
# axis([0, Final_Time, -120, 50]); xlabel("Time (ms)'); ylabel('V (red) & Stimulus (blue)")
# set(ZA, "LineWidth", 2)

trace1 = PlotlyJS.scatter(;x=Time[1], y=100*X[1,:], mode="lines", line_color="red")
trace2 = PlotlyJS.scatter(;x=Ptime, y=SineWave, mode="lines", line_color="blue")
layout = PlotlyJS.Layout(;title="Phase Space", xaxis_range=[-1, .5], yaxis_range=[-1, 1])
PlotlyJS.plot([trace1, trace2])


Stacktrace:
 [1] depwarn(::String, ::Symbol) at ./deprecated.jl:70
 [2] sin(::StepRangeLen{Float64,Base.TwicePrecision{Float64},Base.TwicePrecision{Float64}}) at ./deprecated.jl:57
 [3] include_string(::String, ::String) at ./loading.jl:515
 [4] execute_request(::ZMQ.Socket, ::IJulia.Msg) at /home/vis-528/.julia/v0.6/IJulia/src/execute_request.jl:160
 [5] eventloop(::ZMQ.Socket) at /home/vis-528/.julia/v0.6/IJulia/src/eventloop.jl:8
 [6] (::IJulia.##11#14)() at ./task.jl:335
while loading In[11], in expression starting on line 3


In [12]:

VV = -0.9:0.01:1.5
DVdt = -0.5*((1.37 + 3.67*VV + 2.51*VV.^2).*(VV - 0.55) - Stim/13)./(VV + 0.92)
DRdt = 1.35*VV + 1.03
# figure(2), ZB = plot(VV, DVdt, "k-', VV, DRdt, 'b-', X[1, :], X[2, :], 'r-"); axis([-1, 0.6, 0, 1])

trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="black", name="dV/dt")
trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="blue", name="dR/dt")
trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red", name="Output vs. Input")
layout = PlotlyJS.Layout(;title="Phase Space", xaxis_range=[-1, .5], yaxis_range=[0, 1])
PlotlyJS.plot([trace1, trace2, trace3], layout)

# set(ZB, "LineWidth", 2); axis square
# Spikes = (X[1, 1:Last-1] < 0).*(X[1, 2:Last] >= 0)
# Num_Spikes = sum(Spikes)
# clear X
# Previous = 1
# Next = 1
# When = Time[2:Last].*(Spikes > 0);  #Times at which spikes occur
# Interval = zeros(1, Num_Spikes - 1)
# clear Spikes
# for K = 2:length(When)
# 	if When[K] > 0; 
# 		Interval[Next] = When[K] - When[Previous]
# 		Previous = K; 
# 		Next = Next + 1
# 		end
# end
# clear When
# figure(3); hist(Interval, 100)


In [13]:

Spikes = (X[1, 1:Last-1] .< 0).*(X[1, 2:Last] .>= 0)
Num_Spikes = sum(Spikes)

Previous = 1
Next = 1

When = Time[1][2:Last].*(Spikes .> 0);  # Times at which spikes occur
global When#
global K
global Interval
global Previous
global Next
@show length(When)
Interval = zeros(1, Num_Spikes)
@show size(Interval)
for K = 2:length(When)#length(When)
    try
        
        if When[K] .> 0; 
            Interval[Next] = When[K] - When[Previous]
            Previous = K;
            Next = Next + 1
        end
        catch BoundsError
        @show K
    end
end

length(When) = 25000

In [21]:
@show X[:, 5]

X[:, 5] = [-0.640843, 0.0895314]


2-element Array{Float64,1}:
 -0.640843 
  0.0895314

# HumanNeuron.m

In [43]:

Total_Equations = 2  #Solve for this number of interacting Neurons
DT = 0.04  #Time increment
Final_Time = 400   #Final time value for calculation
Last = Int64(Final_Time/DT + 1)  #Last time step
Time = DT*(0:Last-1)  #Time vector
Tau = 1  #Neural time constants in msec
TauR = 5.6

X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)

WTS = [1 2 2 1]  #Runge-Kutta Coefficient weights
for NU = 1:Total_Equations  #Initialize
    X[NU, :] = zeros(1, Last)  #Vector to store response of Neuron #1
    K[NU, :] = zeros(1, 4)  #Runge-Kutta terms	
    Weights[NU, :] = WTS  #Make into matrix for efficiency in main loop
end
X[1, 1] = -0.754  #Initial conditions here if different from zero
X[2, 1] = 0.279  #Initial conditions here if different from zero
Wt2 = [0 .5 .5 1]  #Second set of RK weights
rkIndex = [1 1 2 3]
Stim = 1#input("Stimulating current strength (0-2): ")


ST = 10.6
for T = 2:Last
  for rk = 1:4  #Fourth Order Runge-Kutta
    XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
    Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade
    
    K[1, rk] = DT/Tau*(-(17.81 + 47.58*XH[1] + 33.8*XH[1]^2)*(XH[1] - 0.48) - 26*XH[2]*(XH[1] + 0.95) + Stim);  
    K[2, rk] = DT/TauR*(-XH[2] + 1.29*XH[1] + 0.79 + 3.3*(XH[1] + 0.38)^2)

 end
    X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
end

trace1 = PlotlyJS.scatter(;x=Time, y=100*X[1, :], mode="lines", line_color="red")
#layout = Layout # xlabel("Time (ms)'); ylabel('Potential (mV)")
p1 = PlotlyJS.plot([trace1])


VV = -0.9:0.01:1.5
DVdt = -0.5*((1.37 + 3.66*VV + 2.6*VV.^2).*(VV - 0.48) - Stim/13)./(VV + 0.95)
DRdt = 1.29*VV + 0.79 + 3.3*(VV + 0.38).^2
@show DRdt[1:10]

trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="black")
trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="blue")
trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2,  :], mode="lines", line_color="red")
layout = PlotlyJS.Layout(;title="dV/dt = 0 isocline (black), dR/dt = 0 isocline (blue) & limit cycle (red", xaxis_range=[-1, 0], yaxis_range=[0, 1])
p2 = PlotlyJS.plot([trace1, trace2, trace3], layout)

# figure(2), ZB = plot(VV, DVdt, "k-', VV, DRdt, 'b-', X[1, :], X[2, :], 'r-"); axis([-1, 0.6, 0, 1])



Spikes = (X[1, 1:Last - 1] .< -0.12).*(X[1, 2:Last] .>= -0.12)
SpkTime = zeros(1, sum(Spikes))
Nspk = 1;  # Number of spike
for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
end
Final = length(SpkTime)
Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
Spike_Rate = mean(Rates)

[p1 p2]



DRdt[1:10] = [0.52132, 0.50023, 0.4798, 0.46003, 0.44092, 0.42247, 0.40468, 0.38755, 0.37108, 0.35527]


# PhaseShift.jl

In [60]:

#Fourth Order Runge-Kutta for N-Dimensional Systems


Total_Neurons = 2;  #Solve for this number of interacting Neurons
DT = 0.02;  #Time increment as fraction of time constant
Final_Time = 20;   #Final time value for calculation
Last = Int64(Final_Time/DT + 1);  #Last time step
Time = DT*(0:Last-1);  #Time vector
Tau = 0.8;  #Neural time constants in msec
TauR = 1.9
WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)

for NU = 1:Total_Neurons;  #Initialize
	X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
	K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
	Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
end


X[1, 1] = -0.70;  #Initial conditions here if different from zero
X[2, 1] = 0.088;  #Initial conditions here if different from zero
Wt2 = [0 .5 .5 1];  #Second set of RK weights
rkIndex = [1 1 2 3]

#********** Change following line for problems
ConstStim = 0.15;  #Constant current for spike train
#**********

Stim = 1#input (Stimulating pulse amplitude (0-2): ")
Pstart = 100# input("Time (ms) for pulse = ")

for T = 2:Last
  for rk = 1:4  #Fourth Order Runge-Kutta
	XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
 	Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade
		
	K[1, rk] = DT/Tau*(-(17.81 + 47.71*XH[1] + 32.63*XH[1]^2)*(XH[1] - 0.55) - 26*XH[2]*(XH[1] + 0.92) + ConstStim + Stim*(Tme >= Pstart).*(Tme <= Pstart + 0.1));  
  	K[2, rk] = DT/TauR*(-XH[2] + 1.35*XH[1] + 1.03)

 end
	X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
end

Ptime = 0:0.1:200
Pulse = -90 + 10*Stim*(Ptime .>= Pstart).*(Ptime .<= Pstart + 0.1)
NX = [0.8 5.9 11.0 16.1]; #Normal spike times
SP = [43 43 43 43]

trace1 = PlotlyJS.scatter(x=Time, y=100*X[1, :], mode="lines", linecolor="red")
trace2 = PlotlyJS.scatter(x=Ptime, y=Pulse, mode="lines", linecolor="blue")
trace3 = PlotlyJS.scatter(x=NX, y=SP, mode="lines", linecolor="green")
layout = PlotlyJS.Layout(title="Phase Resetting (normal spike times at dot()s)", 
                         xaxis_range=[0, Final_Time], yaxis_range=[-90, 50])
#title('Phase Resetting (normal spike times at dot()s)")

p1 = PlotlyJS.plot([trace1, trace2, trace3], layout)

VV = -0.9:0.01:1.5
DVdt = -0.5*((1.37 + 3.67*VV + 2.51*VV.^2).*(VV - 0.55) - ConstStim/13)./(VV + 0.92)
DRdt = 1.35*VV + 1.03

trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="black")
trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="blue")
trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red")
layout = PlotlyJS.Layout(title="Phase Space", xaxis_range=[-1, .6], yaxis_range=[0, 1])

p2 = PlotlyJS.plot([trace1, trace2, trace3], layout)

[p1 p2]
# figure(2), ZB = plot(VV, DVdt, "k-', VV, DRdt, 'b-', X[1, :], X[2, :], 'r-"); axis([-1, 0.6, 0, 1])
# set(ZB, "LineWidth", 2); axis([-.9 .5 0 .6]); axis square


# Morris_Lecar.jl

In [73]:

Total_Equations = 2;  #Solve for this number of interacting Neurons
DT = 0.04;  #Time increment
Final_Time = 100;   #Final time value for calculation
Last = Int64(Final_Time/DT + 1);  #Last time step
Time = DT*(0:Last-1);  #Time vector
Tau = 0.97;  #Neural time constants in msec
TauR = 5.0
WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)

for NU = 1:Total_Equations;  #Initialize
	X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
	K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
	Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
end
X[1, 1] = -0.5;  #Initial conditions here if different from zero
X[2, 1] = 0;  #Initial conditions here if different from zero
Wt2 = [0 .5 .5 1];  #Second set of RK weights
rkIndex = [1 1 2 3]
Stim = 1#input("Stimulating current strength (0-2): ")


ST = 10.6
for T = 2:Last
  for rk = 1:4  #Fourth Order Runge-Kutta
	XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
 	Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade
	
	TauR = 1/cosh((XH[1] - 0.1)/0.14)
	
	#TauR = 0.5; #Remove comment here to use constant tau
	
	K[1, rk] = DT/Tau*(-1/(1 + exp(-(XH[1] + 0.01)/0.075))*(XH[1] - 1.0) - 2*XH[2]*(XH[1] + 0.7) - 0.5*(XH[1] + 0.5) + Stim);  
  	K[2, rk] = DT*0.2/TauR*(-XH[2] + 1/(1 + exp(-(XH[1] - 0.1)/0.07)))
		
 end
	X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
end

trace1 = PlotlyJS.scatter(;x=Time, y=X[1, :], mode="lines", line_color="red", name="Potential(mV)")
layout = PlotlyJS.Layout(title="Potential(mV) vs Time(ms)")
PlotlyJS.plot([trace1], layout)

VV = -0.69:0.01:0.7
DVdt = 0.5*(-(VV - 1)./(1 + exp.(-(VV + 0.01)/0.075)) - 0.5*(VV + 0.5) + Stim)./(VV + 0.7)
DRdt = 1./(1+exp.(-(VV - 0.1)/0.07))


trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="black")
trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="blue")
trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red")
layout = PlotlyJS.Layout(title="dV/dt = 0 isocline (black), dR/dt = 0 isocline (blue) & limit cycle (red)", xaxis_range=[-1, .6], yaxis_range=[0, 1])

p2 = PlotlyJS.plot([trace1, trace2, trace3], layout)

[p1 p2]

# figure(2), ZB = plot(VV, DVdt, "k-', VV, DRdt, 'b-', X[1, :], X[2, :], 'r-"); axis([-0.8, 0.7, -0.2, 0.5])
# set(ZB, "LineWidth", 2); axis square
# title("dV/dt = 0 isocline (black), dR/dt = 0 isocline (blue) & limit cycle (red")
# Spikes = (X[1, 1:Last - 1] < -0.12).*(X[1, 2:Last] >= -0.12)
# SpkTime = zeros(1, sum(Spikes))
# Nspk = 1;  #Number of spike
# for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
# 	if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
# end
# Final = length(SpkTime)
# Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
# Spike_Rate = mean(Rates)


# CanonicalNeuron.jl

In [92]:
Total_Equations = 2;  #Solve for this number of interacting Neurons
DT = 0.1;  #Time increment as fraction of time constant
Final_Time = 200;   #Final time value for calculation
Last = Int64(Final_Time/DT + 1);  #Last time step
Time = DT*(0:Last-1);  #Time vector
TauR = 5
WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

X = Array{Float64}(2, Last)
K = Array{Float64}(2, 4)
Weights = Array{Float64}(2, 4)

for NU = 1:Total_Equations;  #Initialize
	X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
	K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
	X[1, 1] = 0;  #Initial conditions here if different from zero
	X[2, 1] = 0;  #Initial conditions here if different from zero
	Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
end

Wt2 = [0 .5 .5 1];  #Second set of RK weights
rkIndex = [1 1 2 3]
Input = 1#input("Stimulus strength = ")

G = 0.047
P = 0.48


for T = 2:Last
  for rk = 1:4  #Fourth Order Runge-Kutta
	XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
	Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade
		
	K[1, rk] = DT*(-4*(XH[1]^2 - XH[1]/10)*(XH[1] - 1) - XH[2]*(XH[1] + 1/5) + Input);  #Your Equation Here
  	K[2, rk] = DT/TauR*(-XH[2] + 3*XH[1]^2);    #Your Equation Here

 end
	X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6  #Most efficient with weight matrix
end



Xiso = -0.19:0.01:1;  #X for Isoclines
Isocline1 = (-4*(Xiso.^2 - Xiso/10).*(Xiso - 1) + Input)./(Xiso + 1/5);
Isocline2 = 3.*Xiso.^2

trace1 = PlotlyJS.scatter(;x=Time, y=X[1, :], mode="lines", line_color="red", name="Potential(mV)")
layout = PlotlyJS.Layout(title="Potential(mV) vs Time(ms)", xaxis_label="Time (arbitrary units)", yaxis_label="V (Normalized Units)")

p1 = PlotlyJS.plot([trace1], layout)


# trace1 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red")
# trace2 = PlotlyJS.scatter(;x=Xiso, y=Isocline1, mode="lines", line_color="black")
# trace3 = PlotlyJS.scatter(;x=Xiso, y=Isocline2, mode="lines", line_color="blue")
# layout = PlotlyJS.Layout(title="dV/dt = 0 isocline (black), dR/dt = 0 isocline (blue) & limit cycle (red)", xaxis_range=[-1, .6], yaxis_range=[0, 1])

# p2 = PlotlyJS.plot([trace1, trace2, trace3], layout)

# [p1 p2]


# figure(2); Zb = plot(X(1, :), X(2, :), '-r', Xiso, Isocline1, '-k', Xiso, Isocline2, '--k'); set(Zb, 'LineWidth', 2); axis square;
# axis([-0.2 1 -0.2 1]); xlabel('V'); ylabel('R');
